In [15]:
import pandas as pd
import altair as alt
import itertools

alt.data_transformers.enable("vegafusion")
#pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 500)

A useful guide to [Multiclass and multioutput algorithms](https://scikit-learn.org/stable/modules/multiclass.html) indicates that, as we have a single target with cardinality >2, we should use a 'multiclass' estimator.

In [39]:
# Take a peek at the data to get an idea of dtypes...
train_values = pd.read_csv('data/train_values.csv', index_col='building_id', nrows=10)
train_labels = pd.read_csv('data/train_labels.csv', index_col='building_id', nrows=10)
test_values = pd.read_csv('data/test_values.csv', index_col='building_id', nrows=10)

display(train_values.dtypes)

for df in [train_values, train_labels]:
    display(df.shape)
    display(df.head().T)

geo_level_1_id                             int64
geo_level_2_id                             int64
geo_level_3_id                             int64
count_floors_pre_eq                        int64
age                                        int64
area_percentage                            int64
height_percentage                          int64
land_surface_condition                    object
foundation_type                           object
roof_type                                 object
ground_floor_type                         object
other_floor_type                          object
position                                  object
plan_configuration                        object
has_superstructure_adobe_mud               int64
has_superstructure_mud_mortar_stone        int64
has_superstructure_stone_flag              int64
has_superstructure_cement_mortar_stone     int64
has_superstructure_mud_mortar_brick        int64
has_superstructure_cement_mortar_brick     int64
has_superstructure_t

(10, 38)

building_id                            802906 28830  94947  590882 201944
geo_level_1_id                              6      8     21     22     11
geo_level_2_id                            487    900    363    418    131
geo_level_3_id                          12198   2812   8973  10694   1488
count_floors_pre_eq                         2      2      2      2      3
age                                        30     10     10     10     30
area_percentage                             6      8      5      6      8
height_percentage                           5      7      5      5      9
land_surface_condition                      t      o      t      t      t
foundation_type                             r      r      r      r      r
roof_type                                   n      n      n      n      n
ground_floor_type                           f      x      f      f      f
other_floor_type                            q      q      x      x      x
position                                    t      s      t      s      s
plan_configuration                          d      d      d      d      d
has_superstructure_adobe_mud                1      0      0      0      1
has_superstructure_mud_mortar_stone         1      1      1      1      0
has_superstructure_stone_flag               0      0      0      0      0
has_superstructure_cement_mortar_stone      0      0      0      0      0
has_superstructure_mud_mortar_brick         0      0      0      0      0
has_superstructure_cement_mortar_brick      0      0      0      0      0
has_superstructure_timber                   0      0      0      1      0
has_superstructure_bamboo                   0      0      0      1      0
has_superstructure_rc_non_engineered        0      0      0      0      0
has_superstructure_rc_engineered            0      0      0      0      0
has_superstructure_other                    0      0      0      0      0
legal_ownership_status                      v      v      v      v      v
count_families                              1      1      1      1      1
has_secondary_use                           0      0      0      0      0
has_secondary_use_agriculture               0      0      0      0      0
has_secondary_use_hotel                     0      0      0      0      0
has_secondary_use_rental                    0      0      0      0      0
has_secondary_use_institution               0      0      0      0      0
has_secondary_use_school                    0      0      0      0      0
has_secondary_use_industry                  0      0      0      0      0
has_secondary_use_health_post               0      0      0      0      0
has_secondary_use_gov_office                0      0      0      0      0
has_secondary_use_use_police                0      0      0      0      0
has_secondary_use_other                     0      0      0      0      0

(10, 1)

building_id   802906  28830   94947   590882  201944
damage_grade       3       2       3       2       3

In [40]:
objects = train_values.select_dtypes('object')
objects.apply(pd.unique)
object_columns = list(objects.columns)


In [41]:
# The description tells us which are categorical...
categorical_columns = ['land_surface_condition',
                        'foundation_type',
                        'roof_type',
                        'ground_floor_type',
                        'other_floor_type',
                        'position',
                        'plan_configuration',
                        'legal_ownership_status']

In [42]:
# The description tells us which are boolean, and they all happen to start with has_...
boolean_columns = [column for column in train_values.columns if column.startswith('has_')]

In [7]:
# These are ordered whereby: geographic region in which building exists, from 
# largest (level 1) to most specific sub-region (level 3). 
# Possible values: level 1: 0-30, level 2: 0-1427, level 3: 0-12567.
# Nota bene: They may not be independent if lower region id values repeat...
location_columns = ['geo_level_1_id', 'geo_level_2_id', 'geo_level_3_id']

In [43]:
# Excluding boolean_columns and the location_columns, all others are numerical...
numbers = train_values.drop(boolean_columns + location_columns, axis=1).select_dtypes('number')
numerical_columns = list(numbers.columns)
numbers.describe()

count_floors_pre_eq        age  area_percentage  height_percentage  \
count            10.000000  10.000000        10.000000          10.000000   
mean              2.000000  14.000000         7.400000           5.600000   
std               0.471405  11.005049         2.674987           1.505545   
min               1.000000   0.000000         3.000000           4.000000   
25%               2.000000  10.000000         6.000000           5.000000   
50%               2.000000  10.000000         8.000000           5.000000   
75%               2.000000  22.500000         8.000000           6.000000   
max               3.000000  30.000000        13.000000           9.000000   

       count_families  
count            10.0  
mean              1.0  
std               0.0  
min               1.0  
25%               1.0  
50%               1.0  
75%               1.0  
max               1.0

In [50]:
# Geographic region in which building exists, from largest (level 1) to most specific sub-region (level 3). 
# Possible values: level 1: 0-30, level 2: 0-1427, level 3: 0-12567.
# Specific CategoricalDtype are required to keep them as int64...
type1 = pd.CategoricalDtype(categories=range(0, 30 + 1), ordered=False)
type2 = pd.CategoricalDtype(categories=range(0, 1427 + 1), ordered=False)
type3 = pd.CategoricalDtype(categories=range(0, 12567 + 1), ordered=False)

c = itertools.product(categorical_columns, ['category']) # categories_dtype=str, ordered=False
b = itertools.product(boolean_columns, ['boolean'])
dtype = dict(list(c) + list(b) + [('geo_level_1_id', type1), ('geo_level_2_id', type2), ('geo_level_3_id', type3)])

nrows = None # None for all... i.e. 260601

train_values = pd.read_csv('data/train_values.csv', index_col='building_id', dtype=dtype, nrows=nrows)
train_labels = pd.read_csv('data/train_labels.csv', index_col='building_id', nrows=nrows)
test_values = pd.read_csv('data/test_values.csv', index_col='building_id', dtype=dtype, nrows=nrows)

display(train_values.info())
for location_column in location_columns:
    display(train_values[location_column].dtype)

<class 'pandas.core.frame.DataFrame'>
Index: 260601 entries, 802906 to 747594
Data columns (total 38 columns):
 #   Column                                  Non-Null Count   Dtype   
---  ------                                  --------------   -----   
 0   geo_level_1_id                          260601 non-null  category
 1   geo_level_2_id                          260601 non-null  category
 2   geo_level_3_id                          260601 non-null  category
 3   count_floors_pre_eq                     260601 non-null  int64   
 4   age                                     260601 non-null  int64   
 5   area_percentage                         260601 non-null  int64   
 6   height_percentage                       260601 non-null  int64   
 7   land_surface_condition                  260601 non-null  category
 8   foundation_type                         260601 non-null  category
 9   roof_type                               260601 non-null  category
 10  ground_floor_type               

None

CategoricalDtype(categories=range(0, 31), ordered=False, categories_dtype=int64)

CategoricalDtype(categories=range(0, 1428), ordered=False, categories_dtype=int64)

CategoricalDtype(categories=range(0, 12568), ordered=False, categories_dtype=int64)

In [26]:
from ydata_profiling import ProfileReport

profile = train_values.profile_report(
                        title="Richter's Train Dataset Pandas profile",
                        correlations={
                            "auto": {"calculate": True, 'threshold': 0.0, 'warn_high_correlations': True},
                            "pearson": {"calculate": False},
                            "spearman": {"calculate": False},
                            "kendall": {"calculate": False},
                            "phi_k": {"calculate": False},
                            "cramers": {"calculate": False}
                        }
)

profile.to_notebook_iframe() # to_widgets() did not complete in a reasonable time...


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [46]:
possible_categorical_values = {
    'land_surface_condition': ['n', 'o', 't'],
    'foundation_type': ['h', 'i', 'r', 'u', 'w'],
    'roof_type': ['n', 'q', 'x'],
    'ground_floor_type': ['f', 'm', 'v', 'x', 'z'],
    'other_floor_type': ['j', 'q', 's', 'x'],
    'position': ['j', 'o', 's', 't'],
    'plan_configuration': ['a', 'c', 'd', 'f', 'm', 'n', 'o', 'q', 's', 'u'],
    'legal_ownership_status': ['a', 'r', 'v', 'w']
}

display(possible_categorical_values)
display(train_values[categorical_columns].apply(pd.unique))
display(test_values[categorical_columns].apply(pd.unique))

{'land_surface_condition': ['n', 'o', 't'],
 'foundation_type': ['h', 'i', 'r', 'u', 'w'],
 'roof_type': ['n', 'q', 'x'],
 'ground_floor_type': ['f', 'm', 'v', 'x', 'z'],
 'other_floor_type': ['j', 'q', 's', 'x'],
 'position': ['j', 'o', 's', 't'],
 'plan_configuration': ['a', 'c', 'd', 'f', 'm', 'n', 'o', 'q', 's', 'u'],
 'legal_ownership_status': ['a', 'r', 'v', 'w']}

land_surface_condition    ['t', 'o', 'n']
Categories (3, object): ['n', ...
foundation_type           ['r', 'w', 'i', 'u', 'h']
Categories (5, objec...
roof_type                 ['n', 'q', 'x']
Categories (3, object): ['n', ...
ground_floor_type         ['f', 'x', 'v', 'z', 'm']
Categories (5, objec...
other_floor_type          ['q', 'x', 'j', 's']
Categories (4, object): [...
position                  ['t', 's', 'j', 'o']
Categories (4, object): [...
plan_configuration        ['d', 'u', 's', 'q', 'm', 'c', 'a', 'n', 'f', ...
legal_ownership_status    ['v', 'a', 'r', 'w']
Categories (4, object): [...
dtype: object

land_surface_condition    ['t', 'n', 'o']
Categories (3, object): ['n', ...
foundation_type           ['r', 'w', 'u', 'h', 'i']
Categories (5, objec...
roof_type                 ['n', 'x', 'q']
Categories (3, object): ['n', ...
ground_floor_type         ['f', 'v', 'x', 'm', 'z']
Categories (5, objec...
other_floor_type          ['q', 'j', 'x', 's']
Categories (4, object): [...
position                  ['s', 't', 'j', 'o']
Categories (4, object): [...
plan_configuration        ['d', 'u', 'q', 'a', 'c', 'm', 's', 'o', 'f', ...
legal_ownership_status    ['v', 'a', 'w', 'r']
Categories (4, object): [...
dtype: object

In [51]:
# 'geo_level_1_id', 'geo_level_2_id', 'geo_level_3_id'
# TODO: Want to check if values in smaller regions are replicated in larger regions...
# The geo_level_n_id are a good proxy for local conditions that most likely affect the prediction. 
# It is qualatitive (categorical) rather than quantative (should not be scaled). It is specifically nominal 
# rather than ordinal (ordered).
# Although they could be one hot encoded, this will result in large dimensional data.
# 1. OneHotEncoder -> Principal Component Analysis (PCA) to 3 components.
# 



display(train_values[location_columns].describe())

# location = train_values[location_columns].groupby(location_columns[::-1]).value_counts()
# #index = location.to_frame()
# display(location)
# #display(index)

# level0 = location.index.get_level_values(0)#.to_series()
# level1 = location.index.get_level_values(1)#.to_series()
# level2 = location.index.get_level_values(2)#.to_series()

# level0_duplicates = level0[level0.duplicated()]
# level1_duplicates = level1[level1.duplicated()]
# level2_duplicates = level2[level2.duplicated()]


# display(level0_duplicates) # geo_level_3_id, no duplication which means no overlap in geo_level_2_id
# display(level1_duplicates) # geo_level_2_id, duplication as there are N observations per geo_level_1_id
# display(level2_duplicates) # geo_level_1_id, duplication as there are N observations per geo_level_1_id

# train_values.query('geo_level_2_id in @level1_duplicates')[location_columns].groupby('geo_level_3_id').value_counts()

#, location.index.get_level_values(1).has_duplicates, location.index.get_level_values(2).has_duplicates

#index.has_duplicates, location.index.get_level_values(1).has_duplicates, location.index.get_level_values(2).has_duplicates


geo_level_1_id  geo_level_2_id  geo_level_3_id
count           260601          260601          260601
unique              31            1414           11595
top                  6              39             633
freq             24381            4038             651

With 260K+ observations, and according to [Choosing the right estimator](https://scikit-learn.org/stable/tutorial/machine_learning_map/index.html), a good option would be 'Linear SVC'...

In [52]:
alt.Chart(train_values[numerical_columns]).mark_bar().encode(
    x = alt.X(alt.repeat("repeat"), type='quantitative'),
    y = 'count()',
).properties(
    width=100,
    height=100
).repeat(
    repeat=numerical_columns,
    columns=4
)

alt.RepeatChart(...)

In [54]:
import sklearn.utils.multiclass as multiclass
from sklearn.pipeline import make_pipeline, Pipeline, make_union, FeatureUnion, FunctionTransformer
from sklearn.compose import make_column_transformer, ColumnTransformer
from sklearn.decomposition import PCA
from sklearn.feature_selection import SelectKBest
from sklearn.multiclass import OutputCodeClassifier
from sklearn.preprocessing import StandardScaler, OneHotEncoder, TargetEncoder
from sklearn.svm import LinearSVC
from sklearn.metrics import f1_score

target_column = 'damage_grade'
type_of_target = multiclass.type_of_target(train_labels[target_column])
print(f'target variable {target_column} is {type_of_target}...')

# The combination of OneHotEncoder and PCA (Principal Component analysis) for this dataset crashed the kernel on my machine...

# CountEncoder (category_encoders), also called Frequency encoding, useful when there’s a correlation between the frequency of a category and the target variable
# HashingEncoder (category_encoders)
# CatBoostEncoder (catboost)
# TargetEncoder, each category is encoded based on a shrunk estimate of the average target values for observations belonging to the category
# Embedding (tensorflow)

preprocessing = make_pipeline(
    make_union(
        make_pipeline(
            make_column_transformer(
                #(OneHotEncoder(sparse_output=False, handle_unknown="ignore"), location_columns),
                (TargetEncoder(), location_columns),
            ),
            #PCA(n_components=3) # 'mle' Maximum Likelihood Estimation
        ).set_output(transform='pandas'),
        make_column_transformer(
            (OneHotEncoder(sparse_output=False, handle_unknown="ignore"), categorical_columns),
            ("passthrough", numerical_columns),
            ("passthrough", boolean_columns)
        )
    )
).set_output(transform='pandas')

display(preprocessing)

X_train_transformed = preprocessing.fit_transform(train_values, train_labels[target_column])
X_test_transformed = preprocessing.transform(test_values)

target variable damage_grade is multiclass...


Pipeline(steps=[('featureunion',
                 FeatureUnion(transformer_list=[('pipeline',
                                                 Pipeline(steps=[('columntransformer',
                                                                  ColumnTransformer(transformers=[('targetencoder',
                                                                                                   TargetEncoder(),
                                                                                                   ['geo_level_1_id',
                                                                                                    'geo_level_2_id',
                                                                                                    'geo_level_3_id'])]))])),
                                                ('columntransformer',
                                                 ColumnTransformer(transformers=[('onehotencoder',
                                                                                  OneHotEncoder(handle_unknown='ignore',
                                                                                                spars...
                                                                                   'has_superstructure_rc_engineered',
                                                                                   'has_superstructure_other',
                                                                                   'has_secondary_use',
                                                                                   'has_secondary_use_agriculture',
                                                                                   'has_secondary_use_hotel',
                                                                                   'has_secondary_use_rental',
                                                                                   'has_secondary_use_institution',
                                                                                   'has_secondary_use_school',
                                                                                   'has_secondary_use_industry',
                                                                                   'has_secondary_use_health_post',
                                                                                   'has_secondary_use_gov_office',
                                                                                   'has_secondary_use_use_police',
                                                                                   'has_secondary_use_other'])]))]))])

In [55]:
# Nota bene: The kernel crashed with OneHotEncoder/PCA...
display(X_train_transformed.T)

building_id                                           802906    28830   \
pipeline__targetencoder__geo_level_1_id_1           0.086554  0.033635   
pipeline__targetencoder__geo_level_1_id_2            0.66625  0.446438   
pipeline__targetencoder__geo_level_1_id_3           0.247196  0.519923   
pipeline__targetencoder__geo_level_2_id_1                0.0  0.012496   
pipeline__targetencoder__geo_level_2_id_2           0.241716   0.47883   
pipeline__targetencoder__geo_level_2_id_3           0.757796  0.508108   
pipeline__targetencoder__geo_level_3_id_1                0.0  0.091346   
pipeline__targetencoder__geo_level_3_id_2           0.222772  0.716427   
pipeline__targetencoder__geo_level_3_id_3           0.773855   0.19057   
columntransformer__onehotencoder__land_surface_...       0.0       0.0   
columntransformer__onehotencoder__land_surface_...       0.0       1.0   
columntransformer__onehotencoder__land_surface_...       1.0       0.0   
columntransformer__onehotencoder__foundation_ty...       0.0       0.0   
columntransformer__onehotencoder__foundation_ty...       0.0       0.0   
columntransformer__onehotencoder__foundation_ty...       1.0       1.0   
columntransformer__onehotencoder__foundation_ty...       0.0       0.0   
columntransformer__onehotencoder__foundation_ty...       0.0       0.0   
columntransformer__onehotencoder__roof_type_n            1.0       1.0   
columntransformer__onehotencoder__roof_type_q            0.0       0.0   
columntransformer__onehotencoder__roof_type_x            0.0       0.0   
columntransformer__onehotencoder__ground_floor_...       1.0       0.0   
columntransformer__onehotencoder__ground_floor_...       0.0       0.0   
columntransformer__onehotencoder__ground_floor_...       0.0       0.0   
columntransformer__onehotencoder__ground_floor_...       0.0       1.0   
columntransformer__onehotencoder__ground_floor_...       0.0       0.0   
columntransformer__onehotencoder__other_floor_t...       0.0       0.0   
columntransformer__onehotencoder__other_floor_t...       1.0       1.0   
columntransformer__onehotencoder__other_floor_t...       0.0       0.0   
columntransformer__onehotencoder__other_floor_t...       0.0       0.0   
columntransformer__onehotencoder__position_j             0.0       0.0   
columntransformer__onehotencoder__position_o             0.0       0.0   
columntransformer__onehotencoder__position_s             0.0       1.0   
columntransformer__onehotencoder__position_t             1.0       0.0   
columntransformer__onehotencoder__plan_configur...       0.0       0.0   
columntransformer__onehotencoder__plan_configur...       0.0       0.0   
columntransformer__onehotencoder__plan_configur...       1.0       1.0   
columntransformer__onehotencoder__plan_configur...       0.0       0.0   
columntransformer__onehotencoder__plan_configur...       0.0       0.0   
columntransformer__onehotencoder__plan_configur...       0.0       0.0   
columntransformer__onehotencoder__plan_configur...       0.0       0.0   
columntransformer__onehotencoder__plan_configur...       0.0       0.0   
columntransformer__onehotencoder__plan_configur...       0.0       0.0   
columntransformer__onehotencoder__plan_configur...       0.0       0.0   
columntransformer__onehotencoder__legal_ownersh...       0.0       0.0   
columntransformer__onehotencoder__legal_ownersh...       0.0       0.0   
columntransformer__onehotencoder__legal_ownersh...       1.0       1.0   
columntransformer__onehotencoder__legal_ownersh...       0.0       0.0   
columntransformer__passthrough-1__count_floors_...         2         2   
columntransformer__passthrough-1__age                     30        10   
columntransformer__passthrough-1__area_percentage          6         8   
columntransformer__passthrough-1__height_percen...         5         7   
columntransformer__passthrough-1__count_families           1         1   
columntransformer__passthrough-2__has_superstru...      True     False   
colu

In [56]:

# baseline
clf = LinearSVC(random_state=0, dual='auto', max_iter=2000)
clf.fit(X_train_transformed, train_labels[target_column])
y_pred = clf.predict(X_train_transformed)
baseline_micro_f1 = f1_score(train_labels[target_column], y_pred, average='micro')
print(f'Baseline micro f1 {baseline_micro_f1}')

# Create and train the classifier with OutputCode Classifier
clf = OutputCodeClassifier(LinearSVC(random_state=0, dual='auto', max_iter=2000), code_size=2, random_state=0)
clf.fit(X_train_transformed, train_labels[target_column])
y_pred = clf.predict(X_train_transformed)
occ_micro_f1 = f1_score(train_labels[target_column], y_pred, average='micro')
print(f'OCC micro f1 {occ_micro_f1}')

Baseline micro f1 0.7320194473543846
OCC micro f1 0.7303310424748946


# Score History

Baseline micro f1 0.7320194473543846
OCC micro f1 0.7303310424748946

Baseline micro f1 0.63235
OCC micro f1 0.63137

Baseline micro f1 0.5820737449203955
OCC micro f1 0.5829064355086895

In [57]:
from sklearn.model_selection import train_test_split, GridSearchCV, RandomizedSearchCV, KFold
from sklearn.ensemble import HistGradientBoostingRegressor, HistGradientBoostingClassifier
from sklearn.metrics import make_scorer

target_column = 'damage_grade'

#split data into 80% training and 20% test sets
X_train, X_test, y_train, y_test = train_test_split(X_train_transformed, train_labels[target_column], test_size=0.2, random_state=0)

# TODO: Try XGBoost and/or CatBoost

hist_regressor = HistGradientBoostingRegressor(
    random_state=0, categorical_features="from_dtype", early_stopping=True, max_iter=1000
)

hist_classifier = HistGradientBoostingClassifier(
    random_state=0, categorical_features="from_dtype", early_stopping=True, max_iter=1000
)

boosting_params = {
    "max_depth": [3, 8],
    "max_leaf_nodes": [2, 5, 10, 20, 50, 100],
    "learning_rate": [0.01, 1],
}

#cv = KFold(n_splits=4, shuffle=True, random_state=0)
results = []
for model, params in [(hist_regressor, boosting_params), 
                    (hist_classifier, boosting_params)]:
    search = RandomizedSearchCV(
        model, params,
        # scoring='f1_micro', # Classification metrics can't handle a mix of multiclass and continuous targets
        # Nota bene: round the y_pred values as this is a regression/classification problem.
        scoring=make_scorer(lambda y_true, y_pred: f1_score(y_true, y_pred.round(), average='micro'), greater_is_better=True),
        n_jobs=-1,
        return_train_score=True,
        cv=2, # StratifiedKFold/KFold with shuffle=False, 
    ).fit(X_train, y_train)
    result = {"model": type(model), "best_estimator": search.best_estimator_, "cv_results": pd.DataFrame(search.cv_results_)}
    results.append(result)

In [58]:
# 'concat' all cv_results, repeating the 'model' for each value...
# those with prefix of param_...
model_names=map(lambda n: n.__name__, [x['model'] for x in results])
dfs = [x['cv_results'] for x in results]
foo = pd.concat(dfs, keys=model_names, names=['model']).reset_index()
display(foo.T)
params=[column for column in foo.columns if column.startswith('param_')]
alt.Chart(foo).mark_line(point=True).encode(
    x = alt.X(alt.repeat("repeat"), type='quantitative'),
    y = 'mean_test_score:Q',
    color = 'model'
).properties(
    width=100,
    height=100
).repeat(
    repeat=['mean_fit_time'] + params,
)

0   \
model                                     HistGradientBoostingRegressor   
level_1                                                               0   
mean_fit_time                                                    5.0683   
std_fit_time                                                   0.133469   
mean_score_time                                                0.617165   
std_score_time                                                 0.036692   
param_max_leaf_nodes                                                100   
param_max_depth                                                       8   
param_learning_rate                                                   1   
params                {'max_leaf_nodes': 100, 'max_depth': 8, 'learn...   
split0_test_score                                              0.729634   
split1_test_score                                              0.728924   
mean_test_score                                                0.729279   
std_test_score                                                 0.000355   
rank_test_score                                                       9   
split0_train_score                                             0.758557   
split1_train_score                                             0.757252   
mean_train_score                                               0.757905   
std_train_score                                                0.000652   

                                                                     1   \
model                                     HistGradientBoostingRegressor   
level_1                                                               1   
mean_fit_time                                                 58.094998   
std_fit_time                                                   0.150615   
mean_score_time                                                9.640735   
std_score_time                                                 0.129156   
param_max_leaf_nodes                                                 10   
param_max_depth                                                       8   
param_learning_rate                                                0.01   
params                {'max_leaf_nodes': 10, 'max_depth': 8, 'learni...   
split0_test_score                                              0.738997   
split1_test_score                                              0.737001   
mean_test_score                                                0.737999   
std_test_score                                                 0.000998   
rank_test_score                                                       3   
split0_train_score                                              0.73986   
split1_train_score                                             0.739898   
mean_train_score                                               0.739879   
std_train_score                                                0.000019   

                                                                     2   \
model                                     HistGradientBoostingRegressor   
level_1                                                               2   
mean_fit_time                                                  6.718887   
std_fit_time                                                   0.021859   
mean_score_time                                                0.681868   
std_score_time                                                 0.009021   
param_max_leaf_nodes                                                  2   
param_max_depth                                                       8   
param_learning_rate                                                   1   
params                {'max_leaf_nodes': 2, 'max_depth': 8, 'learnin...   
split0_test_score                                              0.728665   
split1_test_score                                              0.726525   
mean_test_score                                                0.727595   
std_test_score   

alt.RepeatChart(...)

In [59]:
from sklearn.metrics import f1_score

for result in results:
    estimator = result['best_estimator']
    y_pred = estimator.predict(X_test).round()
    micro_f1 = f1_score(y_test, y_pred, average='micro')
    print(f'{result["model"].__name__} micro f1 {micro_f1}')
    print(f'{estimator.get_params()}')

HistGradientBoostingRegressor micro f1 0.7437693060378734
{'categorical_features': 'from_dtype', 'early_stopping': True, 'interaction_cst': None, 'l2_regularization': 0.0, 'learning_rate': 0.01, 'loss': 'squared_error', 'max_bins': 255, 'max_depth': 8, 'max_features': 1.0, 'max_iter': 1000, 'max_leaf_nodes': 100, 'min_samples_leaf': 20, 'monotonic_cst': None, 'n_iter_no_change': 10, 'quantile': None, 'random_state': 0, 'scoring': 'loss', 'tol': 1e-07, 'validation_fraction': 0.1, 'verbose': 0, 'warm_start': False}
HistGradientBoostingClassifier micro f1 0.7471844362157288
{'categorical_features': 'from_dtype', 'class_weight': None, 'early_stopping': True, 'interaction_cst': None, 'l2_regularization': 0.0, 'learning_rate': 0.01, 'loss': 'log_loss', 'max_bins': 255, 'max_depth': 8, 'max_features': 1.0, 'max_iter': 1000, 'max_leaf_nodes': 100, 'min_samples_leaf': 20, 'monotonic_cst': None, 'n_iter_no_change': 10, 'random_state': 0, 'scoring': 'loss', 'tol': 1e-07, 'validation_fraction': 0.

HistGradientBoostingRegressor micro f1 0.7437693060378734
{'categorical_features': 'from_dtype', 'early_stopping': True, 'interaction_cst': None, 'l2_regularization': 0.0, 'learning_rate': 0.01, 'loss': 'squared_error', 'max_bins': 255, 'max_depth': 8, 'max_features': 1.0, 'max_iter': 1000, 'max_leaf_nodes': 100, 'min_samples_leaf': 20, 'monotonic_cst': None, 'n_iter_no_change': 10, 'quantile': None, 'random_state': 0, 'scoring': 'loss', 'tol': 1e-07, 'validation_fraction': 0.1, 'verbose': 0, 'warm_start': False}
HistGradientBoostingClassifier micro f1 0.7471844362157288
{'categorical_features': 'from_dtype', 'class_weight': None, 'early_stopping': True, 'interaction_cst': None, 'l2_regularization': 0.0, 'learning_rate': 0.01, 'loss': 'log_loss', 'max_bins': 255, 'max_depth': 8, 'max_features': 1.0, 'max_iter': 1000, 'max_leaf_nodes': 100, 'min_samples_leaf': 20, 'monotonic_cst': None, 'n_iter_no_change': 10, 'random_state': 0, 'scoring': 'loss', 'tol': 1e-07, 'validation_fraction': 0.1, 'verbose': 0, 'warm_start': False}

HistGradientBoostingRegressor micro f1 0.7093110262658046
{'categorical_features': 'from_dtype', 'early_stopping': True, 'interaction_cst': None, 'l2_regularization': 0.0, 'learning_rate': 0.01, 'loss': 'squared_error', 'max_bins': 255, 'max_depth': 8, 'max_features': 1.0, 'max_iter': 1000, 'max_leaf_nodes': 100, 'min_samples_leaf': 20, 'monotonic_cst': None, 'n_iter_no_change': 10, 'quantile': None, 'random_state': 0, 'scoring': 'loss', 'tol': 1e-07, 'validation_fraction': 0.1, 'verbose': 0, 'warm_start': False}
HistGradientBoostingClassifier micro f1 0.7297250628345581
{'categorical_features': 'from_dtype', 'class_weight': None, 'early_stopping': True, 'interaction_cst': None, 'l2_regularization': 0.0, 'learning_rate': 0.01, 'loss': 'log_loss', 'max_bins': 255, 'max_depth': 8, 'max_features': 1.0, 'max_iter': 1000, 'max_leaf_nodes': 100, 'min_samples_leaf': 20, 'monotonic_cst': None, 'n_iter_no_change': 10, 'random_state': 0, 'scoring': 'loss', 'tol': 1e-07, 'validation_fraction': 0.1, 'verbose': 0, 'warm_start': False}

In [61]:
estimator = results[1]['best_estimator']
submission = pd.read_csv("data/submission_format.csv")
submission["damage_grade"] = estimator.predict(X_test_transformed)
submission.to_csv("submission.csv", index=False)